In [1]:
import tensorflow as tf
import numpy as np
import random
import os
import pickle
import gc

# Reproducibility
seed = 42
os.environ['PYTHONHASHSEED'] = str(seed)
random.seed(seed)
np.random.seed(seed)
tf.random.set_seed(seed)

# Optional: disable eager execution (if using graph mode code)
#tf.compat.v1.disable_eager_execution()

# Session config
session_conf = tf.compat.v1.ConfigProto(
    intra_op_parallelism_threads=1,
    inter_op_parallelism_threads=1
)
sess = tf.compat.v1.Session(config=session_conf)

# Set this session as default for everything that follows
# No set_session needed — use a context manager instead
with sess.as_default():
    # your model/code here
    pass

tf.__version__

2025-05-19 11:32:16.050366: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-05-19 11:32:16.060614: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1747654336.070944 1103778 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1747654336.074101 1103778 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1747654336.082930 1103778 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking 

'2.19.0'

In [2]:
os.getcwd()

'/mnt/c/Users/ansel/AppData/Local/Programs/Microsoft VS Code'

In [3]:
os.chdir('/mnt/d/GitHub/WQU-Capstone/notebooks/classes')

os.getcwd()

'/mnt/d/GitHub/WQU-Capstone/notebooks/classes'

### Import Classes

In [4]:
%load_ext autoreload
%aimport class_ForecastingTrader 
%autoreload 1

I0000 00:00:1747654338.178986 1103778 gpu_device.cc:2019] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 9706 MB memory:  -> device: 0, name: NVIDIA GeForce RTX 3060, pci bus id: 0000:01:00.0, compute capability: 8.6


In [5]:
# series_analyser = class_SeriesAnalyser.SeriesAnalyser()
# trader = class_Trader.Trader()
# data_processor = class_DataProcessor.DataProcessor()
forecasting_trader = class_ForecastingTrader.ForecastingTrader()

In [6]:
current_path='/mnt/d/GitHub/WQU-Capstone/notebooks/PCA_75etf'
with open(f'{current_path}/PCA_selected_pairs.pickle', 'rb') as handle: 
    pairs = pickle.load(handle)
len(pairs)

9

## model train

In [7]:
n_in_set = [24, 12, 6]
hidden_nodes_set = [[50], [30], [20], [10]]

hidden_nodes_names = [str(nodes[0])+'*2' if len(nodes) > 1 else str(nodes[0]) for nodes in hidden_nodes_set]

In [8]:
for input_dim in n_in_set:
    for i, hidden_nodes in enumerate(hidden_nodes_set):
        model_config = {"n_in": input_dim,
                        "n_out": 1,
                        "epochs": 500,
                        "hidden_nodes": hidden_nodes,
                        "loss_fct": "mse",
                        "optimizer": "rmsprop",
                        "batch_size": 256,
                        "train_val_split": '2023-01-01',
                        "test_init": '2024-01-01',}
        models = forecasting_trader.train_models(pairs, model_config, model_type='rnn')
        # save models for this configuration
        with open(f'{current_path}/models/lstm/models_n_in-'+str(input_dim)+'_hidden_nodes-'+hidden_nodes_names[i]+'.pkl', 'wb') as f:
            pickle.dump(models, f)

gc.collect()

I0000 00:00:1747654338.269550 1103778 gpu_device.cc:2019] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 9706 MB memory:  -> device: 0, name: NVIDIA GeForce RTX 3060, pci bus id: 0000:01:00.0, compute capability: 8.6
/home/ansel/miniconda3/envs/tf/lib/python3.12/site-packages/keras/src/layers/rnn/rnn.py:200: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ lstm (LSTM)                     │ (None, 50)             │        10,400 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 1)              │            51 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 10,451 (40.82 KB)

 Trainable params: 10,451 (40.82 KB)

...

 Total params: 491 (1.92 KB)

 Trainable params: 491 (1.92 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/500
5/5 ━━━━━━━━━━━━━━━━━━━━ 1s 48ms/step - loss: 0.5279 - mae: 0.5774 - val_loss: 1.5890 - val_mae: 1.0925
Epoch 2/500
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step - loss: 0.4596 - mae: 0.5327 - val_loss: 1.5083 - val_mae: 1.0627
Epoch 3/500
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - loss: 0.4179 - mae: 0.5028 - val_loss: 1.4399 - val_mae: 1.0366
Epoch 4/500
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step - loss: 0.3838 - mae: 0.4771 - val_loss: 1.3763 - val_mae: 1.0117
Epoch 5/500
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - loss: 0.3539 - mae: 0.4537 - val_loss: 1.3148 - val_mae: 0.9870
Epoch 6/500
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - loss: 0.3269 - mae: 0.4318 - val_loss: 1.2541 - val_mae: 0.9618
Epoch 7/500
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - loss: 0.3020 - mae: 0.4112 - val_loss: 1.1936 - val_mae: 0.9359
Epoch 8/500
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - loss: 0.2789 - mae: 0.3922 - val_loss: 1.1330 - val_mae: 0.9090
Epoch 9/500
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step - loss: 0.2574 - mae: 

51278

In [9]:
for input_dim in n_in_set:
    for i, hidden_nodes in enumerate(hidden_nodes_set):
        print('input_dim:', input_dim)

        print(i,' hidden_nodes:', hidden_nodes)

input_dim: 24
0  hidden_nodes: [50]
input_dim: 24
1  hidden_nodes: [30]
input_dim: 24
2  hidden_nodes: [20]
input_dim: 24
3  hidden_nodes: [10]
input_dim: 12
0  hidden_nodes: [50]
input_dim: 12
1  hidden_nodes: [30]
input_dim: 12
2  hidden_nodes: [20]
input_dim: 12
3  hidden_nodes: [10]
input_dim: 6
0  hidden_nodes: [50]
input_dim: 6
1  hidden_nodes: [30]
input_dim: 6
2  hidden_nodes: [20]
input_dim: 6
3  hidden_nodes: [10]
